<a href="https://colab.research.google.com/github/vsubhashini/long-live-the-battery/blob/master/colabs/model_training_battery_life.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Train model and predict

To create data refer to this colab:




In [1]:
!git clone https://github.com/vsubhashini/long-live-the-battery.git

Cloning into 'long-live-the-battery'...
remote: Enumerating objects: 17, done.
remote: Counting objects: 100% (17/17), done.
remote: Compressing objects: 100% (12/12), done.
remote: Total 1448 (delta 6), reused 12 (delta 5), pack-reused 1431
Receiving objects: 100% (1448/1448), 1.14 MiB | 3.69 MiB/s, done.
Resolving deltas: 100% (955/955), done.


In [0]:
import os

from google.colab import files
from google.colab import drive

import argparse
import datetime

import tensorflow as tf
from absl import logging

In [4]:
drive.mount('/content/gdrive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/gdrive


## Point to data in Drive

Download and save pre-processed data (tfrecord) to Drive

1. Download tfrecords folder from here: https://github.com/dsr-18/long-live-the-battery-dataset/tree/master/tfrecords
2. Save the tfrecords folder in Drive. (Here it is saved in a folder named battery-life within "My Drive")

My Drive > battery-life > data > tfrecords

The code below modifies variables to point to the data in the Drive folder.

In [0]:
DATA_HOME = "/content/gdrive/My Drive/battery-life/data"

In [6]:
!ls

gdrive	long-live-the-battery  sample_data


In [0]:
os.chdir('./long-live-the-battery')

In [0]:
import trainer.constants as cst

In [9]:
#@title Change the directory
cst.DATASETS_DIR=DATA_HOME+'/tfrecords'
print(cst.DATASETS_DIR)
cst.DATA_DIR=DATA_HOME
print(cst.DATA_DIR)

/content/gdrive/My Drive/battery-life/data/tfrecords
/content/gdrive/My Drive/battery-life/data


In [0]:
import trainer.data_pipeline as dp
import trainer.split_model as split_model
import trainer.full_cnn_model as full_cnn_model
from trainer.callbacks import CustomCheckpoints

cst.DATASETS_DIR=DATA_HOME+'/tfrecords'
cst.DATA_DIR=DATA_HOME
cst.TRAIN_SET = os.path.join(cst.DATASETS_DIR, 'train', '*tfrecord')  # regexp files for the training set
cst.TEST_SET = os.path.join(cst.DATASETS_DIR, 'test', '*tfrecord')  # regexp for the test set
cst.SECONDARY_TEST_SET = os.path.join(cst.DATASETS_DIR, 'secondary_test', '*tfrecord')  # regexp for the secondary test set
cst.BIG_TRAIN_SET = os.path.join(cst.DATASETS_DIR, 'train_big', '*tfrecord')  	 # regexp for the combined training set (train + 1st test sets)
cst.SCALING_FACTORS_DIR = os.path.join(cst.DATASETS_DIR, 'scaling_factors.csv')  # location for scaling factors for tfrecords files

## Train model

In [0]:
#@title Define model training loop and arguments

def get_args():
    """Argument parser.

    Returns:
        Dictionary of arguments.
    """
    parser = argparse.ArgumentParser()
    parser.add_argument(
        '--job-dir',
        type=str,
        default=cst.BASE_DIR,
        help='local or GCS location for writing checkpoints and exporting models')
    parser.add_argument(
        '--data-dir-train',
        type=str,
        default=cst.TRAIN_SET,
        help='local or GCS location for reading TFRecord files for the training set')
    parser.add_argument(
        '--data-dir-validate',
        type=str,
        default=cst.TEST_SET,
        help='local or GCS location for reading TFRecord files for the validation set')
    parser.add_argument(
        '--tboard-dir',         # no default so we can construct dynamically with timestamp
        type=str,
        help='local or GCS location for reading TensorBoard files')
    parser.add_argument(
        '--saved-model-dir',    # no default so we can construct dynamically with timestamp
        type=str,
        help='local or GCS location for saving trained Keras models')
    parser.add_argument(
        '--num-epochs',
        type=int,
        default=3,
        help='number of times to go through the data, default=3')
    parser.add_argument(
        '--batch-size',
        default=32,
        type=int,
        help='number of records to read during each training step, default=16')
    parser.add_argument(
        '--window-size',
        default=20,
        type=int,
        help='window size for sliding window in training sample generation, default=100')
    parser.add_argument(
        '--shift',
        default=5,
        type=int,
        help='shift for sliding window in training sample generation, default=20')
    parser.add_argument(
        '--stride',
        default=1,
        type=int,
        help='stride inside sliding window in training sample generation, default=1')
    parser.add_argument(
        '--verbosity',
        choices=['DEBUG', 'ERROR', 'FATAL', 'INFO', 'WARN'],
        default='DEBUG')
    parser.add_argument(
        '--loss',
        default='mean_squared_error',
        type=str,
        help='loss function used by the model, default=mean_squared_error')
    parser.add_argument(
        '--shuffle',
        default=True,
        type=bool,
        help='shuffle the batched dataset, default=True'
    )
    parser.add_argument(
        '--shuffle-buffer',
        default=500,
        type=int,
        help='Bigger buffer size means better shuffling but longer setup time. Default=500'
    )
    parser.add_argument(
        '--save-from',
        default=80,
        type=int,
        help='epoch after which model checkpoints are saved, default=80'
    )
    parser.add_argument(
        '--model',
        default='split_model',
        type=str,
        help='The type of model to use, default="split_model", options="split_model", "full_cnn_model"'
    )
    args, _ = parser.parse_known_args()
    return args


def train_and_evaluate(args, tboard_dir, hparams=None):
    """Trains and evaluates the Keras model.

    Uses the Keras model defined in model.py and trains on data loaded and
    preprocessed in data_pipeline.py. Saves the trained model in TensorFlow SavedModel
    format to the path defined in part by the --job-dir argument.

    Args:
    args: dictionary of arguments - see get_args() for details
    """
    # Config datasets for consistent usage
    ds_config = dict(window_size=args.window_size,
                     shift=args.shift,
                     stride=args.stride,
                     batch_size=args.batch_size)
    ds_train_path = args.data_dir_train
    ds_val_path = args.data_dir_validate

    # create model
    if args.model == 'split_model':
        print("Using split model!")
        model = split_model.create_keras_model(window_size=ds_config["window_size"],
                                               loss=args.loss,
                                               hparams_config=hparams)
    if args.model == 'full_cnn_model':
        print("Using full cnn model!")
        model = full_cnn_model.create_keras_model(window_size=ds_config["window_size"],
                                                  loss=args.loss,
                                                  hparams_config=hparams)
    
    # Calculate steps_per_epoch_train, steps_per_epoch_test
    # This is needed, since for counting repeat has to be false
    steps_per_epoch_train = calculate_steps_per_epoch(data_dir=ds_train_path, dataset_config=ds_config)
    
    steps_per_epoch_validate = calculate_steps_per_epoch(data_dir=ds_val_path, dataset_config=ds_config)
    
    # load datasets
    dataset_train = dp.create_dataset(data_dir=ds_train_path,
                                      window_size=ds_config["window_size"],
                                      shift=ds_config["shift"],
                                      stride=ds_config["stride"],
                                      batch_size=ds_config["batch_size"])
    
    dataset_validate = dp.create_dataset(data_dir=ds_val_path,
                                         window_size=ds_config["window_size"],
                                         shift=ds_config["shift"],
                                         stride=ds_config["stride"],
                                         batch_size=ds_config["batch_size"])
    
    # if hparams is passed, we're running a HPO-job
    if hparams:
        checkpoint_callback = CustomCheckpoints(save_last_only=True,
                                                log_dir=tboard_dir,
                                                dataset_path=ds_val_path,
                                                dataset_config=ds_config,
                                                save_eval_plot=False)
    else:
        checkpoint_callback = CustomCheckpoints(save_best_only=True,
                                                start_epoch=args.save_from,
                                                log_dir=tboard_dir,
                                                dataset_path=ds_val_path,
                                                dataset_config=ds_config,
                                                save_eval_plot=False)
    callbacks = [
        tf.keras.callbacks.TensorBoard(log_dir=tboard_dir,
                                       histogram_freq=0,
                                       write_graph=False,
                                       ),
        checkpoint_callback,
    ]

    model.summary()
    
    # train model
    history = model.fit(
        dataset_train, 
        epochs=args.num_epochs,
        steps_per_epoch=steps_per_epoch_train,
        validation_data=dataset_validate,
        validation_steps=steps_per_epoch_validate,
        verbose=2,
        callbacks=callbacks)
    
    mae_current = min(history.history["val_mae_current_cycle"])
    mae_remaining = min(history.history["val_mae_remaining_cycles"])
    return mae_current, mae_remaining


def calculate_steps_per_epoch(data_dir, dataset_config):
    temp_dataset = dp.create_dataset(data_dir=data_dir,
                                     window_size=dataset_config["window_size"],
                                     shift=dataset_config["shift"],
                                     stride=dataset_config["stride"],
                                     batch_size=dataset_config["batch_size"],
                                     repeat=False)
    steps_per_epoch = 0
    for batch in temp_dataset:
        steps_per_epoch += 1
    return steps_per_epoch


def get_tboard_dir():
    run_timestr = datetime.datetime.now().strftime("%Y%m%d-%H%M%S")
    if args.tboard_dir is None:
        tboard_dir = os.path.join(cst.TENSORBOARD_DIR, "jobs", run_timestr)
    else:
        tboard_dir = args.tboard_dir
    return tboard_dir


#if __name__ == '__main__':
#    args = get_args()
#    logging.set_verbosity(args.verbosity)
#    train_and_evaluate(args, get_tboard_dir())

In [0]:
args = get_args()
logging.set_verbosity(args.verbosity)

In [23]:
#@title view training parameters
args

Namespace(batch_size=32, data_dir_train='/content/gdrive/My Drive/battery-life/data/tfrecords/train/*tfrecord', data_dir_validate='/content/gdrive/My Drive/battery-life/data/tfrecords/test/*tfrecord', job_dir='./', loss='mean_squared_error', model='split_model', num_epochs=600, save_from=80, saved_model_dir=None, shift=5, shuffle=True, shuffle_buffer=500, stride=1, tboard_dir=None, verbosity='DEBUG', window_size=20)

In [24]:
train_and_evaluate(args, get_tboard_dir())

Using split model!
Model: "model_2"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
Qdlin (InputLayer)              [(None, 20, 1000, 1) 0                                            
__________________________________________________________________________________________________
Tdlin (InputLayer)              [(None, 20, 1000, 1) 0                                            
__________________________________________________________________________________________________
detail_concat (Concatenate)     (None, 20, 1000, 2)  0           Qdlin[0][0]                      
                                                                 Tdlin[0][0]                      
__________________________________________________________________________________________________
convolution (TimeDistributed)   (None, 20, 334, 32)  608         detail_c

(108.78113555908203, 114.64087677001953)

In [25]:
!ls Graph/jobs/20200524-004931/checkpoints/last_epoch_loss_0.00688290735706687

assets	saved_model.pb	variables


In [0]:
#@title Copy saved model to Drive
!cp -R Graph/jobs/20200524-004931/checkpoints/last_epoch_loss_0.00688290735706687* ../gdrive/My\ Drive/battery-life/saved_model/

In [29]:
!ls ../gdrive/My\ Drive/battery-life/saved_model/

last_epoch_loss_0.00688290735706687  last_epoch_loss_0.028139576315879822


In [30]:
!ls Graph/jobs/2020*/train/

Graph/jobs/20200524-004623/train/:
events.out.tfevents.1590281210.8cd16bc171a0.124.7037.v2    plugins
events.out.tfevents.1590281210.8cd16bc171a0.profile-empty

Graph/jobs/20200524-004739/train/:
events.out.tfevents.1590281266.8cd16bc171a0.124.15012.v2   plugins
events.out.tfevents.1590281266.8cd16bc171a0.profile-empty

Graph/jobs/20200524-004931/train/:
events.out.tfevents.1590281379.8cd16bc171a0.124.37614.v2   plugins
events.out.tfevents.1590281379.8cd16bc171a0.profile-empty


In [20]:
#@title View model training loss in tensorboard
%load_ext tensorboard
%tensorboard --logdir Graph

The tensorboard extension is already loaded. To reload it, use:
  %reload_ext tensorboard


Reusing TensorBoard on port 6006 (pid 574), started 0:01:26 ago. (Use '!kill 574' to kill it.)

<IPython.core.display.Javascript object>

## Make predictions

In [0]:
import json
from random import randint
import os

import flask
import numpy as np
import plotly
import plotly.graph_objs as go
import tensorflow as tf
from server.plot import plot_single_prediction
from server.clippy import Clippy, clipped_relu
from trainer.custom_metrics_losses import mae_current_cycle, mae_remaining_cycles

In [0]:
#@title Point to saved model directory
NUM_SAMPLES = 6
#MODEL_DIR = "Graph/jobs/20200524-004931/checkpoints/last_epoch_loss_0.00688290735706687/"
MODEL_DIR = "/content/gdrive/My Drive/battery-life/saved_model/last_epoch_loss_0.00688290735706687/"
SAMPLES_DIR = "static/samples"

In [0]:
#@title prediction and plotting functions
def make_prediction(model, cycle_data):
    cycles = { 'Qdlin': np.array(json.loads(cycle_data['Qdlin'])),
                'Tdlin': np.array(json.loads(cycle_data['Tdlin'])),
                'IR': np.array(json.loads(cycle_data['IR'])),
                'Discharge_time': np.array(json.loads(cycle_data['Discharge_time'])),
                'QD': np.array(json.loads(cycle_data['QD']))
            }

    predictions = model.predict(cycles)

    print("Returning predictions:")
    print(type(predictions))
    print(predictions)
    return predictions
    
def make_plot(model, predictions):
    predictions = np.array(predictions)
    # The prediction endpoint can handle batches of battery data per request,
    # but for now we visualize only the first data example.
    first_pred = predictions[0]
    window_size = model.input_shape[0][1]
    scaling_factors_dict = {"Remaining_cycles": 2159.0}
    mean_cycle_life = 674  # calculated from training set
    figure = plot_single_prediction(first_pred,
                                  window_size,
                                  scaling_factors_dict,
                                  mean_cycle_life)
    return figure

In [0]:
model = tf.keras.models.load_model(MODEL_DIR, custom_objects={'clippy': Clippy(clipped_relu),
                                                              'mae_current_cycle': mae_current_cycle,
                                                              'mae_remaining_cycles': mae_remaining_cycles})

## Load sample json and predict

1. Convert example tfrecord files to json examples using this script: https://github.com/vsubhashini/long-live-the-battery/blob/master/generate_json_samples_from_train.py

2. Save the json files in Drive. Here they are saved in My Drive > battery-life > data > sample_prediction_json

In [0]:
#@title Load sample json file
json_file_sample = os.path.join(DATA_HOME, 'sample_prediction_json/sample_input_1.json')

In [36]:
with open(json_file_sample, 'r') as infd:
  json_data = json.load(infd)
#print(json_data)
predictions_soh_rul= make_prediction(model, json_data)

Returning predictions:
<class 'numpy.ndarray'>
[[0.05725262 0.5115012 ]]


In [37]:
figure = make_plot(model, predictions_soh_rul)
figure.show()

## Upload your own JSON and predict

In [38]:
#@title upload your own json file
files.upload()

Saving sample_input_4.json to sample_input_4.json


{'sample_input_4.json': b'{"Qdlin": "[[[[3.663664392661303e-05], [3.663664392661303e-05], [3.663664392661303e-05], [3.663664392661303e-05], [3.663664392661303e-05], [3.663664392661303e-05], [3.663664392661303e-05], [3.663664392661303e-05], [3.663664392661303e-05], [3.663664392661303e-05], [3.663664392661303e-05], [3.663664392661303e-05], [3.663664392661303e-05], [3.663664392661303e-05], [3.663664392661303e-05], [3.663664392661303e-05], [3.663664392661303e-05], [3.663664392661303e-05], [3.663664392661303e-05], [3.663664392661303e-05], [3.663664392661303e-05], [5.113689257996157e-05], [0.0001819052267819643], [0.00031267356825992465], [0.00044344188063405454], [0.0005742101930081844], [0.0007049785344861448], [0.0008357468759641051], [0.0009661117801442742], [0.0009661117801442742], [0.0009661117801442742], [0.0009661117801442742], [0.0009661117801442742], [0.0009661117801442742], [0.0009661117801442742], [0.0009661117801442742], [0.0009661117801442742], [0.0009661117801442742], [0.00096

In [0]:
json_file_sample = './sample_input_4.json'

In [40]:
with open(json_file_sample, 'r') as infd:
  json_data = json.load(infd)
#print(json_data)
predictions_soh_rul= make_prediction(model, json_data)

Returning predictions:
<class 'numpy.ndarray'>
[[0.03717928 0.318325  ]]


In [41]:
figure = make_plot(model, predictions_soh_rul)
figure.show()